# Decision Tree

----------------------------------------------Concept---------------------------------------------------------------

In Decision Tree:
    1) Internal node ----->feature(or attribute)
    2) The branch----> decision rule
    3) Each leaf node--->outcome. 
    4) The topmost node (root node) learns to partition based on  attribute value. 

The time complexity of decision trees --->A function of the number of "records" and number of "attributes" in data

It works in this way :
    1)Select best Feature with feature selection methods(e.g. Information Gain, Gini Index, Gain Ratio) and put it as root node
    2) Split the data into smaller subset based on this node 
    3) do 1 and 2 for every subset recursively until : there aren't any feature or no more instances remain.

----------------------------------------------Implementation-------------------------------------------------------

dataset preperation :


In [1]:
import numpy as np
from sklearn.cluster import MeanShift, estimate_bandwidth
import pandas as pd


def mean_shift_cluster(dataset_df, cluster_padding_index=0, price_column_name='Price'):
    x = dataset_df[price_column_name]
    X = np.array(list(zip(x, np.zeros(len(x)))), dtype=np.int)
    bandwidth = estimate_bandwidth(X, quantile=0.1)
    ms = MeanShift(bandwidth=bandwidth, bin_seeding=True)
    ms.fit(X)
    labels = ms.labels_
    cluster_centers = ms.cluster_centers_

    labels_unique = np.unique(labels)
    n_clusters_ = len(labels_unique)

    cluster_dists = ''
    for k in range(n_clusters_):
        my_members = labels == k
        cluster_dists += "cluster {0}: {1}\n".format(k + cluster_padding_index, len(X[my_members, 0]))
    print(cluster_dists)

    # TODO: save outputs
    dataset_clustered = dataset_df
    dataset_clustered['price_cluster'] = 0
    for k in range(n_clusters_):
        my_members = labels == k
        dataset_clustered['price_cluster'][my_members] = cluster_padding_index + k
    return dataset_clustered
def price_cluster(dataset, name,price_threshold=None):
    
    # price threshold to filter
    dataset_upper_price_threshold_final_clusters = []
    if price_threshold != None:
        dataset_upper_price_threshold = dataset[dataset['Price'] < price_threshold]
    else:
        dataset_upper_price_threshold = dataset

    x = dataset_upper_price_threshold['Price']

    data = mean_shift_cluster(dataset_upper_price_threshold)
    # print clusters
    result_clusters = list(set(list(data['price_cluster'])))
    cluster_names = {}
    cluster_minis = {}
    price_clusters_str = ''
    for c in result_clusters:
        head = 30 * '*' + 'cluster {}:'.format(c)
        price_clusters_str += head + '\n'
        mini = data[data['price_cluster'] == c]['Price'].min()
        maxi = data[data['price_cluster'] == c]['Price'].max()

        price_clusters_str += 'min: {}\n'.format(mini)
        price_clusters_str += 'max: {}\n'.format(maxi)

        cluster_names[c] = str(mini) + '-' + str(maxi)
         

     
     
    data["cluster_names"] = data["price_cluster"].map(cluster_names)
    
    data.to_csv('data/{}_price_clustered.csv'.format(name))



dataset_name='laptop_data'
dataset = pd.read_csv('data/{}.csv'.format(dataset_name))
price_cluster(dataset,name=dataset_name)

/tmp/ipykernel_52247/684683358.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  X = np.array(list(zip(x, np.zeros(len(x)))), dtype=np.int)
/tmp/ipykernel_52247/684683358.py:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataset_clustered['price_cluster'][my_members] = cluster_padding_index + k


cluster 0: 352
cluster 1: 261
cluster 2: 240
cluster 3: 180
cluster 4: 150
cluster 5: 68
cluster 6: 25
cluster 7: 16
cluster 8: 3
cluster 9: 4
cluster 10: 1
cluster 11: 1
cluster 12: 1
cluster 13: 1



In [2]:
data_clustered=pd.read_csv('data/laptop_data_price_clustered.csv')
# remove instances with cluster 6 to 13 to remove outliers
data_clustered=data_clustered[~data_clustered['price_cluster'].isin([6,7,8,9,10,11,12,13])]

In [3]:
import pandas as pd
pd.options.mode.chained_assignment = None
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
from sklearn import metrics

df= data_clustered
df.head()

Unnamed: 0  Unnamed: 0.1 Company   TypeName  Inches  \
0           0             0   Apple  Ultrabook    13.3   
1           1             1   Apple  Ultrabook    13.3   
2           2             2      HP   Notebook    15.6   
3           3             3   Apple  Ultrabook    15.4   
4           4             4   Apple  Ultrabook    13.3   

                     ScreenResolution                         Cpu   Ram  \
0  IPS Panel Retina Display 2560x1600        Intel Core i5 2.3GHz   8GB   
1                            1440x900        Intel Core i5 1.8GHz   8GB   
2                   Full HD 1920x1080  Intel Core i5 7200U 2.5GHz   8GB   
3  IPS Panel Retina Display 2880x1800        Intel Core i7 2.7GHz  16GB   
4  IPS Panel Retina Display 2560x1600        Intel Core i5 3.1GHz   8GB   

                Memory                           Gpu  OpSys  Weight  \
0            128GB SSD  Intel Iris Plus Graphics 640  macOS  1.37kg   
1  128GB Flash Storage        Intel HD Graphics 6000  macOS  1.34kg   
2            256GB SSD         Intel HD Graphics 620  No OS  1.86kg   
3            512GB SSD            AMD Radeon Pro 455  macOS  1.83kg   
4            256GB SSD  Intel Iris Plus Graphics 650  macOS  1.37kg   

         Price  price_cluster                   cluster_names  
0   71378.6832              3       66280.31999999999-85248.0  
1   47895.5232              1                33566.4-48964.32  
2   30636.0000              0      9270.72-33513.119999999995  
3  135195.3360              5  111593.8944-135195.33599999998  
4   96095.8080              4             85672.1088-111355.2

In [4]:

X =df[df.columns[2:11]]
y =df["cluster_names"]
# convert categorical to label-encoding
for c in list(X.columns):
    X[c]=X[c].astype('category')
    X[c] = X[c].cat.codes 


In [5]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.1, random_state=1) 

Training

In [6]:
# train
clf_dt = DecisionTreeClassifier()
clf_dt = clf_dt.fit(X_train,y_train) 
# predict
y_pred = clf_dt.predict(X_test)
print("Accuracy:",metrics.accuracy_score(y_test, y_pred))


Accuracy: 0.6428571428571429


-----------------------------------------------Visualizing-----------------------------------

In [7]:
from sklearn.tree import export_graphviz
from six import StringIO
from IPython.display import Image  
import pydotplus
feature_cols=df.columns[2:11]
class_names=list(set(list(y)))
dot_data = StringIO()
export_graphviz(clf_dt, out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True,feature_names = feature_cols,class_names=class_names)
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
graph.write_png('laptop.png')
Image(graph.create_png())

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.64889 to fit

dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.64889 to fit

